In [5]:
import pandas as pd 
import numpy as np 
import csv as csv 
import glob 
import pickle
import collections
from datetime import datetime 
import matplotlib.pyplot as plt 
import re

%matplotlib inline

In [6]:
#victimIP = "71.126.222.64"
#to_drop = ['<->', 'total_bytes', 'total_frames']
#names = ['src', '<->', 'dest', 'in_frames', 'in_bytes', 'out_frames', 'out_bytes', 'total_frames', 'total_bytes', 'rel_start', 'duration']

In [27]:
# Begin dataframe by importing the total data, which will have all IPs
#protocol_names = ['total' + "_" + name for name in names]
#print(protocol_names)
#protocol_to_drop = ['total' + "_" + name for name in to_drop]
passive_files = glob.glob('resources/smallpassive*.csv')
d = collections.defaultdict(dict)
for i in range(len(passive_files)):
    result = re.search('_(.*).tshark', passive_files[i])
    protocol = result.group(1)
    if "PORTS" in protocol:
        continue
    passive_df = pd.read_csv(passive_files[i])
    for j, row in passive_df.iterrows():
        if row.outframes > 0:
            if row.duration != 0:
                d[row.src, row.dst][protocol] = [row.outbytes/row.duration, row.outframes/row.duration]
        if row.inframes > 0:
            if row.duration != 0:
                d[row.dst, row.src][protocol] = [row.inbytes/row.duration, row.inframes/row.duration]

In [ ]:
print(d)

In [53]:
rowlist = []
arr = [-1] * 12

for key, value in d.iteritems():
    arr[0] = key[0]
    arr[1] = key[1]
    arr[2] = 'passive'
    arr[3] = value.get('total', [0, 0])[0]
    arr[4] = value.get('total', [0, 0])[1]
    arr[5] = value.get('icmp', [0, 0])[0]
    arr[6] = value.get('icmp', [0, 0])[1]
    arr[7] = value.get('tcp', [0, 0])[0]
    arr[8] = value.get('tcp', [0, 0])[1]
    arr[9] = value.get('with_tcpsyn', [0, 0])[0]
    arr[10] = value.get('with_tcpsyn', [0, 0])[1]
    arr[11] = 0
    rowlist.append(arr)
    
df = pd.DataFrame(rowlist, columns=('src', 'dst', 'label', 'total_out_bytes_rate', 'total_out_frames_rate', 'icmp_out_bytes_rate', 'icmp_out_frames_rate', 'tcp_out_bytes_rate', 'tcp_out_frames_rate', 'with_tcpsyn_out_bytes_rate', 'with_tcpsyn_out_frames_rate', 'tcp_ports_used'))

print(df.to_string())

                 src             dst    label  total_out_bytes_rate  total_out_frames_rate  icmp_out_bytes_rate  icmp_out_frames_rate  tcp_out_bytes_rate  tcp_out_frames_rate  with_tcpsyn_out_bytes_rate  with_tcpsyn_out_frames_rate  tcp_ports_used
0      196.109.12.46  215.158.239.50  passive           2088.409328              22.624434                    0                     0         2088.409328            22.624434                           0                            0               0
1      196.109.12.46  215.158.239.50  passive           2088.409328              22.624434                    0                     0         2088.409328            22.624434                           0                            0               0
2      196.109.12.46  215.158.239.50  passive           2088.409328              22.624434                    0                     0         2088.409328            22.624434                           0                            0               0
3      1

In [49]:
# Pickle the data for later use:
with open('passive_df_pickled.pickle', 'wb') as handle:
    pickle.dump(df, handle)